In [3]:
import pandas as pd
import matplotlib.pyplot as plt
from statsmodels.stats.contingency_tables import Table2x2
import numpy as np
import folium
from folium.plugins import MarkerCluster
import re
import requests
import time


# find the coordinates of INgushetia to better search for the public places in it

In [ ]:
import requests

def get_bounds_for_location(location_name, api_key):
    """Get the latitude, longitude, and bounds for a given location using Google Geocoding API."""
    base_url = "https://maps.googleapis.com/maps/api/geocode/json"
    params = {
        'address': location_name,
        'key': api_key
    }
    response = requests.get(base_url, params=params)
    results = response.json()

    if results.get("status") == "OK":
        location = results['results'][0]['geometry']['location']
        latitude = location['lat']
        longitude = location['lng']
        
        viewport = results['results'][0]['geometry']['viewport']
        north_east = (viewport['northeast']['lat'], viewport['northeast']['lng'])
        south_west = (viewport['southwest']['lat'], viewport['southwest']['lng'])
        
        return latitude, longitude, north_east, south_west
    else:
        print("Error:", results.get("error_message", "No results found"))
        return None, None, None, None

api_key = 'ask_me_for_apikey'
location_name = "Ingushetia, Russia"

latitude, longitude, north_east, south_west = get_bounds_for_location(location_name, api_key)
if latitude and longitude:
    print(f"The coordinates of {location_name} are Latitude: {latitude}, Longitude: {longitude}")
    print(f"Northeast bounds: {north_east}, Southwest bounds: {south_west}")
else:
    print("Failed to get coordinates and bounds.")


## USe google API to fetch the data about public places in Ingushetia

In [2]:


def geocode_location(api_key, location_name):
    geocode_url = "https://maps.googleapis.com/maps/api/geocode/json"
    params = {'address': location_name, 'key': api_key}
    response = requests.get(geocode_url, params=params)
    results = response.json()
    if results.get("status") == "OK":
        location = results['results'][0]['geometry']['location']
        return location['lat'], location['lng']
    else:
        print("Geocode Error:", results.get("error_message", "Unknown error"))
        return None, None

def find_places(api_key, location, place_type):
    places_url = "https://maps.googleapis.com/maps/api/place/nearbysearch/json"
    places = []
    params = {
        'key': api_key,
        'location': f"{location[0]},{location[1]}",
        'radius': 50000,  
        'type': place_type
    }

    response = requests.get(places_url, params=params)
    results = response.json()

    while True:
        places.extend(results['results'])
        if 'next_page_token' in results:
            params['pagetoken'] = results['next_page_token']
            time.sleep(2)  
            response = requests.get(places_url, params=params)
            results = response.json()
        else:
            break

    return places

api_key = 'ask_me_for_apikey'

location_name = "Ingushetia, Russia"
location = geocode_location(api_key, location_name)

place_types = ['school', 'hospital', 'restaurant', 'cafe', 'mosque']

places_df = pd.DataFrame(columns=['place', 'latitude', 'longitude'])

if location:
    for place_type in place_types:
        places = find_places(api_key, location, place_type)
        temp_df = pd.DataFrame(places)
        temp_df = temp_df[['name', 'geometry']].copy()
        temp_df['place'] = place_type
        temp_df['latitude'] = temp_df['geometry'].apply(lambda x: x['location']['lat'])
        temp_df['longitude'] = temp_df['geometry'].apply(lambda x: x['location']['lng'])
        temp_df = temp_df.drop(columns=['geometry', 'name'])
        places_df = pd.concat([places_df, temp_df], ignore_index=True)
else:
    print("Could not geocode the specified location.")

print(places_df.head())
places_df.to_csv('places_lat_long.csv')



    place   latitude  longitude
0  school  43.432174  44.770490
1  school  43.431800  44.770211
2  school  43.469431  44.798980
3  school  43.475620  44.804729
4  school  43.305641  44.897362


## draw a map to plot car accidents and public places

In [7]:

accident_data = pd.read_csv('final_data.csv')
places_data = pd.read_csv('places_lat_long.csv')

accident_data = accident_data[accident_data['point'].str.contains('None') == False]
accident_data['latitude'] = accident_data['point'].apply(lambda x: float(re.search(r'lat: ([\d\.\-]+),', x).group(1)))
accident_data['longitude'] = accident_data['point'].apply(lambda x: float(re.search(r'long: ([\d\.\-]+)', x).group(1)))

center_lat, center_lon = 43.4051698, 44.82029989999999

map = folium.Map(location=[center_lat, center_lon], zoom_start=9)

north_east = [43.6158489, 45.1956928]
south_west = [42.6148929, 44.477352]

map.fit_bounds([south_west, north_east])
map_center = [accident_data['latitude'].mean(), accident_data['longitude'].mean()]
map = folium.Map(location=map_center, zoom_start=12)

marker_cluster = MarkerCluster().add_to(map)

for idx, row in accident_data.iterrows():
    folium.CircleMarker(
        location=(row['latitude'], row['longitude']),
        radius=5,
        color='black',
        fill=True,
        fill_color='black',
        fill_opacity=0.6,
        popup=f"Accident Severity: {row['severity']}"
    ).add_to(marker_cluster)

# Place markers with custom icons
for idx, row in places_data.iterrows():
    icon_url = f"{row['place']}_icon.png"  
    icon = folium.CustomIcon(icon_url, icon_size=(28, 30))
    folium.Marker(
        location=(row['latitude'], row['longitude']),
        icon=icon,
        popup=row['place']
    ).add_to(marker_cluster)

map.save('enhanced_map.html')


### for each car accident, map the nearby public place that was found by the google API previousely

In [9]:
import pandas as pd
import geopandas as gpd
from shapely.geometry import Point
from shapely.ops import nearest_points

accident_data = pd.read_csv('final_data.csv')
places_data = pd.read_csv('places_lat_long.csv')

accident_data = accident_data[accident_data['point'].str.contains('None') == False]
accident_data['latitude'] = accident_data['point'].apply(lambda x: float(re.search(r'lat: ([\d\.\-]+),', x).group(1)))
accident_data['longitude'] = accident_data['point'].apply(lambda x: float(re.search(r'long: ([\d\.\-]+)', x).group(1)))
accident_data['geometry'] = accident_data.apply(lambda row: Point(row['longitude'], row['latitude']), axis=1)
places_data['geometry'] = places_data.apply(lambda row: Point(row['longitude'], row['latitude']), axis=1)

accident_gdf = gpd.GeoDataFrame(accident_data, geometry='geometry')
places_gdf = gpd.GeoDataFrame(places_data, geometry='geometry')

accident_gdf.set_crs(epsg=4326, inplace=True)
places_gdf.set_crs(epsg=4326, inplace=True)

accident_gdf = accident_gdf.to_crs(epsg=3857)
places_gdf = places_gdf.to_crs(epsg=3857)

def find_nearby_place(accident_point, places_gdf):
    buffered = accident_point.buffer(500)  # 500 meters near the accident
    nearby_places = places_gdf[places_gdf.intersects(buffered)]
    if not nearby_places.empty:
        nearest_place = nearest_points(accident_point, nearby_places.unary_union)
        place_type = places_gdf.loc[places_gdf['geometry'] == nearest_place[1], 'place'].iloc[0]
        return place_type
    return None

accident_gdf['nearby_public'] = accident_gdf['geometry'].apply(find_nearby_place, places_gdf=places_gdf)

accident_gdf = accident_gdf.to_crs(epsg=4326)
accident_gdf['nearby_public'] = accident_gdf['nearby_public'].replace('cafe', 'restaurant')

accident_gdf.to_csv('final_data.csv', index=False)

### Draw another map

In [24]:


lat_long_extracted = accident_data['point'].str.extract(r'lat: (?P<latitude>[-\d\.]+), long: (?P<longitude>[-\d\.]+)')

lat_long_extracted['latitude'] = lat_long_extracted['latitude'].astype(float)
lat_long_extracted['longitude'] = lat_long_extracted['longitude'].astype(float)

gdf = gpd.GeoDataFrame(
    accident_data, 
    geometry=gpd.points_from_xy(lat_long_extracted['longitude'], lat_long_extracted['latitude']),
    crs="EPSG:4326"
)

base_map = gdf.explore(
    marker_type="circle",
    marker_kwds={"radius": 5, "fill": True, "fillOpacity": 0.7, "color": "blue"},
    tooltip=["severity", "datetime"],
    popup=True
)
base_map